In [1]:
# This notebook is about self-written peak to peak detection.
# MNE has own peak to peak detection in annotate_amplitude, but it used different settings and the process 
# of calculation there is not yet clear. We may use their way or may keep this one.


#Load data, filter, make folders
import numpy as np
import plotly.graph_objects as go
import pandas as pd
import mne
import configparser
import ancpbids

from main_meg_qc import save_derivative_html, sanity_check, initial_stuff


In [2]:
config = configparser.ConfigParser()
config.read('settings.ini')
data_file='/Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/sub_HT05ND16/210811/mikado-1.fif'
#data_file='/Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/ds004276/sub-001/meg/sub-001_task-words_meg.fif'
sid='001'

df_epochs, epochs_mg, channels, raw_bandpass, raw_bandpass_resamp, raw_cropped, raw = initial_stuff(config, data_file)
m_or_g_chosen = ['mags', 'grads']

m_or_g_chosen = sanity_check(m_or_g_chosen, channels)

if len(m_or_g_chosen) == 0: 
    raise ValueError('No channels to analyze. Check presence of mags and grads in your data set and parameter do_for in settings.')



Opening raw data file /Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/sub_HT05ND16/210811/mikado-1.fif...
    Read a total of 8 projection items:
        magn8_iasoff_68deg.fif : PCA-v1 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v2 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v3 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v4 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v5 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v6 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v7 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v8 (1 x 306)  idle
    Range : 1809000 ... 3375999 =   1809.000 ...  3375.999 secs
Ready.
Opening raw data file /Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/sub_HT05ND16/210811/mikado-2.fif...
    Read a total of 8 projection items:
        magn8_iasoff_68deg.fif : PCA-v1 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v2 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v3 (1 x 30

/Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/Functions/main_meg_qc.py:45: RuntimeWarning: This filename (/Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/sub_HT05ND16/210811/mikado-1.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, _meg.fif, _eeg.fif, _ieeg.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz, _meg.fif.gz, _eeg.fif.gz or _ieeg.fif.gz
  raw = mne.io.read_raw_fif(data_file)


        magn8_iasoff_68deg.fif : PCA-v8 (1 x 306)  idle
    Range : 3376000 ... 4942999 =   3376.000 ...  4942.999 secs
Ready.
Opening raw data file /Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/data/sub_HT05ND16/210811/mikado-3.fif...
    Read a total of 8 projection items:
        magn8_iasoff_68deg.fif : PCA-v1 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v2 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v3 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v4 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v5 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v6 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v7 (1 x 306)  idle
        magn8_iasoff_68deg.fif : PCA-v8 (1 x 306)  idle
    Range : 4943000 ... 5198999 =   4943.000 ...  5198.999 secs
Ready.
Trigger channel has a non-zero initial value of 18 (consider using initial_event=True to detect this event)
9 events found
Event IDs: [ 9 19 20 21 22 23]
Not setting metadata
9 matching events 

/Users/jenya/Local Storage/Job Uni Rieger lab/MEG QC code/Functions/data_load_and_folders.py:118: RuntimeWarning: Trigger channel contains negative values, using absolute value. If data were acquired on a Neuromag system with STI016 active, consider using uint_cast=True to work around an acquisition bug
  events = mne.find_events(data, stim_channel=stim_channel, min_duration=event_dur)


In [3]:
# Separate data for mags and grads in 2 arrays.

#data_channels=raw_bandpass_resamp.get_data(picks = channels)

data_mags = raw_bandpass_resamp.get_data(picks = channels['mags'])
data_grads = raw_bandpass_resamp.get_data(picks = channels['grads'])

sfreq = raw_bandpass_resamp.info['sfreq']
print(sfreq, len(data_mags), len(data_grads))

1000.0 102 204


In [4]:
#EXAMPLE: find peaks of the first magnetometer channel:

from mne.preprocessing import peak_finder

thresh=(max(data_mags[0]) - min(data_mags[0])) / 1.7 #THRESHOLD FOR IDENTIFICATION ADJUST HERE
# The amount above surrounding data for a peak to be identified. Larger values mean the algorithm 
# is more selective in finding peaks. If None, use the default of (max(x0) - min(x0)) / 4.

pos_peak_locs, pos_peak_magnitudes = peak_finder(data_mags[0], extrema=1, thresh=thresh) #positive peaks
neg_peak_locs, neg_peak_magnitudes = peak_finder(data_mags[0], extrema=-1, thresh=thresh) #negative peaks

duration=60
t=np.arange(0, duration, 1/sfreq) 
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=data_mags[0], name='data'));
fig.add_trace(go.Scatter(x=t[pos_peak_locs], y=pos_peak_magnitudes, mode='markers', name='+peak'));
fig.add_trace(go.Scatter(x=t[neg_peak_locs], y=neg_peak_magnitudes, mode='markers', name='-peak'));
fig.update_layout(
    title={
    'text': "First magnetometer: peaks detected",
    'y':0.85,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'},
    xaxis_title="Time in seconds",
    yaxis = dict(
        showexponent = 'all',
        exponentformat = 'e'))
    
fig.show()


#https://www.codegrepper.com/code-examples/python/go.Scatter+no+line

Found 2 significant peaks
Found 3 significant peaks


In [5]:
#EXAMPLE part2: Now find pairs of peaks (pair of neg+positive) and calculate mean over these pairs:

pair_dist_sec=5 #max distance between neg and pos peak to count them as pair, in sec
pair_dist=pair_dist_sec*sfreq

pairs_magnitudes=[]
pairs_locs=[]

for posit_pair_ind, posit_pair in enumerate(pos_peak_locs):
    #find all negative peaks which lay at the set distance from positive ones
    neg_pair_ind=np.where(np.logical_and(neg_peak_locs>=posit_pair-pair_dist/2, neg_peak_locs<=posit_pair+pair_dist/2))
    if neg_pair_ind[0].size != 0: #if there are negative peaks - save pos+negative into pairs
        pairs_locs.append([pos_peak_locs[posit_pair_ind], neg_peak_locs[neg_pair_ind[0][0]]])
        pairs_magnitudes.append([pos_peak_magnitudes[posit_pair_ind], neg_peak_magnitudes[neg_pair_ind[0][0]]])
    #else:
        #print ('No pair detected')
if len(pairs_magnitudes)<1:
    print('No pairs of peaks found, try diffren distance between min and max.')

amplitude=np.zeros(len(pairs_magnitudes),)
for i, pair in enumerate(pairs_magnitudes):
    #print(pair)
    amplitude[i]=pair[0]-pair[1]

mean_amplitude=np.mean(amplitude)


#This for plotting only:
list_pairs_locs = [i for sub in pairs_locs for i in sub]
list_pairs_magnitudes = [i for sub in pairs_magnitudes for i in sub]


fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=data_mags[0], name='data'));
fig.add_trace(go.Scatter(x=t[list_pairs_locs], y=list_pairs_magnitudes, mode='markers', name='pair'));
fig.update_layout(
    title={
    'text': "First magnetometer: PAIRS of peaks detected",
    'y':0.85,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'},
    xaxis_title="Time in seconds",
    yaxis = dict(
        showexponent = 'all',
        exponentformat = 'e'))
    
fig.show()

print('Amplitudes:', amplitude)
print('Mean amplititude: ', mean_amplitude)


Amplitudes: [7.66105651e-12]
Mean amplititude:  7.661056512923471e-12


In [6]:
def neighbour_peak_amplitude(pair_dist_sec: float, sfreq: int, pos_peak_locs:np.ndarray, neg_peak_locs:np.ndarray, pos_peak_magnitudes: np.ndarray, neg_peak_magnitudes: np.ndarray) -> float:

    ''' Function finds a pair: postive+negative peak and calculates the amplitude between them. 
    If no neighbour is found withing given distance - this peak is skipped. 
    If several neighbours are found - several pairs are created. 
    As the result a mean peak-to-peak distance is calculated over all detected pairs for given chunck of data
    
    Args:
    pair_dist_sec (float): maximum distance in seconds which is allowed for negative+positive peaks to be detected as a pair 
    sfreq: sampling frequency of data. Attention to which data is used! original or resampled.
    pos_peak_locs (np.ndarray): output of peak_finder (Python) function - positions of detected Positive peaks
    neg_peak_locs (np.ndarray): output of peak_finder (Python) function - positions of detected Negative peaks
    pos_peak_magnitudes (np.ndarray): output of peak_finder (Python) function - magnitudes of detected Positive peaks
    neg_peak_magnitudes (np.ndarray): output of peak_finder (Python) function - magnitudes of detected Negative peaks

    Returns:
    (float): mean value over all detected peak pairs for this chunck of data.
    '''

    pair_dist=pair_dist_sec*sfreq
    pairs_magnitudes=[]
    pairs_locs=[]

    for posit_pair_ind, posit_pair in enumerate(pos_peak_locs):
        neg_pair_ind=np.where(np.logical_and(neg_peak_locs>=posit_pair-pair_dist/2, neg_peak_locs<=posit_pair+pair_dist/2))
        if neg_pair_ind[0].size != 0:
            pairs_locs.append([pos_peak_locs[posit_pair_ind], neg_peak_locs[neg_pair_ind[0][0]]])
            pairs_magnitudes.append([pos_peak_magnitudes[posit_pair_ind], neg_peak_magnitudes[neg_pair_ind[0][0]]])

    if len(pairs_magnitudes)==0:
        return np.nan

    amplitude=np.zeros(len(pairs_magnitudes),)
    for i, pair in enumerate(pairs_magnitudes):
        amplitude[i]=pair[0]-pair[1]

    return np.mean(amplitude)

In [7]:
def peak_amplitude_per_epoch(mg_names: list, df_epoch_mg: pd.DataFrame, sfreq: int, n_events: int, thresh_lvl: float, pair_dist_sec: float) -> pd.DataFrame:

    '''Function calculates peak-to-peak amplitude for every epoch and every channel (mag or grad).

    Args:
    mg_names (list of tuples): channel name + its index
    df_epoch_mg (pd. Dataframe): data frame containing data for all epochs for mags  or grads
    sfreq: sampling frequency of data. Attention to which data is used! original or resampled.
    n_events (int): number of events in this peace of data
    thresh_lvl (float): defines how high or low need to peak to be to be detected, this can also be changed into a sigle value later
        used in: max(data_ch_epoch) - min(data_ch_epoch)) / thresh_lvl 
    pair_dist_sec (float): maximum distance in seconds which is allowed for negative+positive peaks to be detected as a pair 

    Returns:
    df_pp_ampl_mg (pd.DataFrame): contains the mean peak-to-peak aplitude for each epoch for each channel

    '''
    
    dict_mg = {}

    mg_only_names=[n[0] for n in mg_names]

    epoch_numbers=[ep for ep in range(n_events)]
    for ep in epoch_numbers: #loop over each epoch
        rows_for_ep = [row for row in df_epoch_mg.iloc if row.epoch == ep] #take all rows of 1 epoch, all channels.
  
        peak_ampl_epoch=[]
        for ch_name in mg_only_names: #loop over channel names
            data_ch_epoch = [row_mg[ch_name] for row_mg in rows_for_ep] #take the data for 1 epoch for 1 channel

            thresh=(max(data_ch_epoch) - min(data_ch_epoch)) / thresh_lvl 
            #can also change the whole thresh to a single number setting

            pos_peak_locs, pos_peak_magnitudes = peak_finder(data_ch_epoch, extrema=1, thresh=thresh, verbose=False) #positive peaks
            neg_peak_locs, neg_peak_magnitudes = peak_finder(data_ch_epoch, extrema=-1, thresh=thresh, verbose=False) #negative peaks
            
            pp_ampl=neighbour_peak_amplitude(pair_dist_sec, sfreq, pos_peak_locs, neg_peak_locs, pos_peak_magnitudes, neg_peak_magnitudes)
            peak_ampl_epoch.append(pp_ampl)

        dict_mg[ep] = peak_ampl_epoch

    df_pp_ampl_mg = pd.DataFrame(dict_mg, index=mg_only_names)

    return df_pp_ampl_mg 

In [8]:
def peak_amplitude_all_data(data: mne.io.Raw, channels: list, sfreq: int, thresh_lvl: float, pair_dist_sec: float) -> pd.DataFrame:

    '''Function calculates peak-to-peak amplitude over the entire data set for every channel (mag or grad).

    Args:
    mg_names (list of tuples): channel name + its index
    df_epoch_mg (pd. Dataframe): data frame containing data for all epochs for mags  or grads
    sfreq: sampling frequency of data. Attention to which data is used! original or resampled.
    n_events (int): number of events in this peace of data
    thresh_lvl (float): defines how high or low need to peak to be to be detected, this can also be changed into a sigle value later
        used in: max(data_ch_epoch) - min(data_ch_epoch)) / thresh_lvl 
    pair_dist_sec (float): maximum distance in seconds which is allowed for negative+positive peaks to be detected as a pair 

    Returns:
    df_pp_ampl_all (pd.DataFrame): contains the mean peak-to-peak amplitude for each epoch for each channel

    '''
    
    dict_mg = {}
    #print(channels, len(channels))

    data_channels=data.get_data(picks = channels)

    peak_ampl=[]
    for one_ch_data in data_channels: #loop over channel names

        thresh=(max(one_ch_data) - min(one_ch_data)) / thresh_lvl 
        #can also change the whole thresh to a single number setting

        pos_peak_locs, pos_peak_magnitudes = peak_finder(one_ch_data, extrema=1, thresh=thresh, verbose=False) #positive peaks
        neg_peak_locs, neg_peak_magnitudes = peak_finder(one_ch_data, extrema=-1, thresh=thresh, verbose=False) #negative peaks
        
        pp_ampl=neighbour_peak_amplitude(pair_dist_sec, sfreq, pos_peak_locs, neg_peak_locs, pos_peak_magnitudes, neg_peak_magnitudes)
        peak_ampl.append(pp_ampl)

    #df_pp_ampl_all = pd.DataFrame(peak_ampl, index=channels)

    return peak_ampl

In [9]:
#Peak-to-Peak amplitudes over all data in case no epoching can be done

peak_ampl = peak_amplitude_all_data(raw_cropped, channels['mags'], sfreq, thresh_lvl=3, pair_dist_sec=0.9)
print(peak_ampl)



[nan, nan, nan, 4.152698513793285e-12, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 3.6707115146358485e-12, 3.130378720843564e-12, 2.9160213449024933e-12, 3.2318496680346033e-12, 3.13291549452334e-12, 3.0187606789334207e-12, 3.3669328664826744e-12, 2.8855800607451815e-12, 2.951536176419357e-12, 2.954072950099133e-12, 2.7092742900007506e-12, 2.517747877177664e-12, 2.7752304056749262e-12, 2.7845319091674383e-12, nan, 2.975635526377229e-12, 2.849304197124385e-12, 2.796792981953022e-12, 2.833576200309774e-12, 2.955341336939021e-12, 3.1735038733997557e-12, 3.110084531405356e-12, 3.2419967627537072e-12, 3.304147717908219e-12, 3.117694852444684e-12, 3.141794202402556e-12, 2.8197215132894588e-12, 3.0606174446497244e-12, 2.8779697397058536e-12, 3.2394599890739312e-12, 2.795524595113134e-12, 3.129110334003676e-12, nan, 2.825965879270446e-12, 3.858221369132623e-12, 4.299343546128028e-12, 4.205202041771679e-12, 3.938087460484237e-12, 3.6351966831189847e-12, nan, nan, nan, nan, nan, 

In [11]:

from universal_plots import boxplot_std_hovering_plotly, boxplot_channel_epoch_hovering_plotly
from universal_html_report import make_std_peak_report

sid='001'
m_or_g_chosen = ['mags', 'grads']

m_or_g_title = {
'grads': 'Gradiometers',
'mags': 'Magnetometers'}

ptp_manual_section = config['PTP_manual']
pair_dist_sec = ptp_manual_section.getfloat('pair_dist_sec')
ptp_thresh_lvl = ptp_manual_section.getint('ptp_thresh_lvl')

peak_ampl = {}
figs = {}
fig_path = {}
fig_name = {}
list_of_figure_paths = []
list_of_figures = []
list_of_figure_descriptions = []

for m_or_g in m_or_g_chosen:

    peak_ampl[m_or_g] = peak_amplitude_all_data(raw_cropped, channels[m_or_g], sfreq, thresh_lvl=3, pair_dist_sec=0.9)
    figs[m_or_g], fig_path[m_or_g], fig_name[m_or_g] = boxplot_std_hovering_plotly(std_data=peak_ampl[m_or_g], ch_type=m_or_g_title[m_or_g], channels=channels[m_or_g], sid=sid, what_data = 'peaks')
    list_of_figure_paths.append(fig_path[m_or_g])
    list_of_figures.append(figs[m_or_g])
    list_of_figure_descriptions.append(fig_name[m_or_g])
    list_of_figure_paths.append(fig_path)

[nan, nan, nan, 4.152698513793285e-12, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 3.6707115146358485e-12, 3.130378720843564e-12, 2.9160213449024933e-12, 3.2318496680346033e-12, 3.13291549452334e-12, 3.0187606789334207e-12, 3.3669328664826744e-12, 2.8855800607451815e-12, 2.951536176419357e-12, 2.954072950099133e-12, 2.7092742900007506e-12, 2.517747877177664e-12, 2.7752304056749262e-12, 2.7845319091674383e-12, nan, 2.975635526377229e-12, 2.849304197124385e-12, 2.796792981953022e-12, 2.833576200309774e-12, 2.955341336939021e-12, 3.1735038733997557e-12, 3.110084531405356e-12, 3.2419967627537072e-12, 3.304147717908219e-12, 3.117694852444684e-12, 3.141794202402556e-12, 2.8197215132894588e-12, 3.0606174446497244e-12, 2.8779697397058536e-12, 3.2394599890739312e-12, 2.795524595113134e-12, 3.129110334003676e-12, nan, 2.825965879270446e-12, 3.858221369132623e-12, 4.299343546128028e-12, 4.205202041771679e-12, 3.938087460484237e-12, 3.6351966831189847e-12, nan, nan, nan, nan, nan, 

[3.4799615509621345e-11, 4.166225525156713e-11, 4.185333242183761e-11, 3.0991135585286684e-11, 3.319635605271415e-11, 3.1332557358977005e-11, 3.0020141531489775e-11, 3.702710881969234e-11, 2.392654413360402e-11, 3.191581867387027e-11, 3.0103960228569497e-11, 3.190910728157775e-11, 2.932555439575982e-11, 2.3610542409318816e-11, 2.996895621160078e-11, 2.7646251068978433e-11, 3.0484966386668594e-11, 3.5393048984102864e-11, 2.760600619589821e-11, 2.2157525182815213e-11, 2.133619923954213e-11, 2.3843354389582455e-11, 2.4141984401146083e-11, 3.5519704685885247e-11, 2.2069930978758018e-11, 2.3627510662208536e-11, 2.811595910185247e-11, 2.376046180172013e-11, 2.7753550915002002e-11, 2.267117559409307e-11, 2.4710955037645348e-11, 2.5166329519217796e-11, 2.4950442536401316e-11, 2.3230686060996536e-11, 2.625538111324329e-11, 2.7023846347220854e-11, 2.3452737802205684e-11, 2.116635333936792e-11, 2.4894428906762746e-11, 2.563788187938407e-11, 2.0958082697831083e-11, 2.1378857106602434e-11, 2.335282

In [11]:
dfs_pp_ampl_all['mags']

0
MEG0111           NaN
MEG0121           NaN
MEG0131           NaN
MEG0141  4.152699e-12
MEG0211           NaN
...               ...
MEG2541  4.549996e-12
MEG2611  3.742828e-12
MEG2621  4.194302e-12
MEG2631  4.247753e-12
MEG2641  3.666906e-12

[102 rows x 1 columns]

In [32]:
list_of_figure_paths

['../derivatives/sub-001/megqc/figures/Stds_all_data_Magnetometers.html',
 {'mags': '../derivatives/sub-001/megqc/figures/Stds_all_data_Magnetometers.html',
  'grads': '../derivatives/sub-001/megqc/figures/Stds_all_data_Gradiometers.html'},
 '../derivatives/sub-001/megqc/figures/Stds_all_data_Gradiometers.html',
 {'mags': '../derivatives/sub-001/megqc/figures/Stds_all_data_Magnetometers.html',
  'grads': '../derivatives/sub-001/megqc/figures/Stds_all_data_Gradiometers.html'}]

In [8]:
df_pp_ampl_mags=peak_amplitude_per_epoch(mg_names=channels['mags'], df_epoch_mg=df_epochs_mags, sfreq=sfreq, n_events=n_events, thresh_lvl=2, pair_dist_sec=0.5)

df_pp_ampl_grads=peak_amplitude_per_epoch(mg_names=channels['grads'], df_epoch_mg=df_epochs_grads, sfreq=sfreq, n_events=n_events, thresh_lvl=2, pair_dist_sec=0.5)


In [9]:
df_pp_ampl_mags

0             1             2             3             4  \
MEG0111  6.781290e-13  6.715646e-13  7.210071e-13  5.649438e-13  6.845961e-13   
MEG0121  4.812784e-13  4.726253e-13  4.271365e-13  4.236875e-13  4.141979e-13   
MEG0131  4.027888e-13  4.251910e-13  4.168233e-13  4.255956e-13  4.756329e-13   
MEG0141  6.727289e-13  6.235556e-13  6.483888e-13  6.344024e-13  5.289104e-13   
MEG0211  5.458623e-13  4.712811e-13  5.394367e-13  6.285017e-13  6.464918e-13   
...               ...           ...           ...           ...           ...   
MEG2541  1.079591e-12  1.061480e-12  9.380751e-13  9.881405e-13  9.896877e-13   
MEG2611  6.925077e-13  6.999841e-13  6.233010e-13  5.163528e-13  5.638595e-13   
MEG2621  1.113809e-12  6.258345e-13  9.253349e-13  7.834433e-13  7.990114e-13   
MEG2631  9.285461e-13  6.328654e-13  9.138394e-13  1.155526e-12  8.077903e-13   
MEG2641  5.686062e-13  4.989846e-13  6.964512e-13  6.999360e-13  4.842905e-13   

                    5  
MEG0111  4.059534e-13  
MEG0121  3.779354e-13  
MEG0131  4.797741e-13  
MEG0141  4.944836e-13  
MEG0211  5.126610e-13  
...               ...  
MEG2541  8.723879e-13  
MEG2611  6.070601e-13  
MEG2621           NaN  
MEG2631  7.558506e-13  
MEG2641  5.074808e-13  

[102 rows x 6 columns]

In [10]:
#plot using new universal plotting function:

from universal_plots import boxplot_channel_epoch_hovering_plotly

fig_m_pp_ampl_epoch, fig_path_m_pp_ampl_epoch=boxplot_channel_epoch_hovering_plotly(df_mg=df_pp_ampl_mags, ch_type='Magnetometers', sid='1', what_data='peaks')
fig_g_pp_ampl_epoch, fig_path_g_pp_ampl_epoch=boxplot_channel_epoch_hovering_plotly(df_mg=df_pp_ampl_grads, ch_type='Gradiometers', sid='1', what_data='peaks')

fig_m_pp_ampl_epoch.show()
fig_g_pp_ampl_epoch.show()

In [12]:
from universal_html_report import make_std_peak_report
import configparser

config = configparser.ConfigParser()
config.read('settings.ini')

list_of_figure_paths=[fig_path_m_pp_ampl_epoch, fig_path_g_pp_ampl_epoch]

make_std_peak_report(sid='1', what_data='peaks', list_of_figure_paths=list_of_figure_paths, config=config)

In [ ]:
def MEG_peaks_manual(sid:str, config, channels:list, filtered_d_resamp: mne.io.Raw, m_or_g_chosen):
    #UNFINISHED

    PTP_manual_section = config['PTP_manual']

    # from Peaks_meg_qc import peak_amplitude_per_epoch as pp_epoch 
    ptp_manual_section = config['PTP_manual']
    pair_dist_sec = ptp_manual_section.getint('pair_dist_sec') 
    thresh_lvl = ptp_manual_section.getint('thresh_lvl')

    sfreq = filtered_d_resamp.info['sfreq']
    df_pp_ampl_mags=peak_amplitude_per_epoch(mg_names=mags, df_epoch_mg=df_epochs_mags, sfreq=sfreq, n_events=n_events, thresh_lvl=thresh_lvl, pair_dist_sec=pair_dist_sec)
    df_pp_ampl_grads=peak_amplitude_per_epoch(mg_names=grads, df_epoch_mg=df_epochs_grads, sfreq=sfreq, n_events=n_events, thresh_lvl=thresh_lvl, pair_dist_sec=pair_dist_sec)

    from universal_plots import boxplot_channel_epoch_hovering_plotly
    _, fig_path_m_pp_ampl_epoch=boxplot_channel_epoch_hovering_plotly(df_mg=df_pp_ampl_mags, ch_type='Magnetometers', sid='1', what_data='peaks')
    _, fig_path_g_pp_ampl_epoch=boxplot_channel_epoch_hovering_plotly(df_mg=df_pp_ampl_grads, ch_type='Gradiometers', sid='1', what_data='peaks')

    from universal_html_report import make_std_peak_report
    list_of_figure_paths=[fig_path_m_pp_ampl_epoch, fig_path_g_pp_ampl_epoch]
    make_std_peak_report(sid=sid, what_data='peaks', list_of_figure_paths=list_of_figure_paths)